In [1]:
# Stop warnings
# -------------
import warnings
warnings.filterwarnings("ignore")

# General imports
# ---------------
import os
import sys
import json
import glob
import numpy as np
import h5py
import pandas as pd
opj = os.path.join

# Get inputs
# ----------
subject = 'sub-001'
task = 'GazeCenterFS'
preproc = 'fmriprep_dct_pca'

# Define analysis parameters
with open('mri_analysis/settings.json') as f:
    json_s = f.read()
    analysis_info = json.loads(json_s)

In [2]:
# Define folders and settings
# ---------------------------
base_dir = analysis_info['base_dir']
h5_dir = "{base_dir}/pp_data/{subject}/gauss/h5".format(base_dir = base_dir, subject = subject)


# load deriv data
r2_dict = {}
for roi in analysis_info['rois']:
    
    h5_file = h5py.File("{h5_dir}/{roi}_{task}_{preproc}.h5".format(h5_dir = h5_dir, roi = roi, task = task, preproc = preproc),'r')
    deriv_data = h5_file['{folder_alias}/derivatives'.format(folder_alias = 'pRF')]

    r2_dict.update({roi:deriv_data[:,0]})

# make a dataframe with different array size
df = pd.DataFrame(dict([ (k,pd.Series(v)) for k,v in r2_dict.items() ]))

In [37]:
# to do
# adapt hover

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

template_specs = dict(  axes_color="rgba(0, 0, 0, 1)",          # figure axes color
                        axes_width=0,                           # figureaxes line width
                        axes_font_size=15,                      # font size of axes
                        bg_col="rgba(255, 255, 255, 1)",        # figure background color
                        font='Helvetica',                       # general font used
                        title_font_size=30,                     # font size of titles
                        )

fig_template=go.layout.Template()
fig_template.data.violin = [go.Violin(  box_visible=False,
                                        points=False,
                                        opacity=1,
                                        line_color= "rgba(0, 0, 0, 1)",
                                        fillcolor="rgba(200, 200, 200, 0.5)",
                                        line_width=2,
                                        width=0.8,
                                        marker_symbol='x',
                                        marker_opacity=0.5,
                                        hoveron='violins',
                                        meanline_visible=True,
                                        meanline_color="rgba(0, 0, 0, 1)",
                                        meanline_width=2,
                                        )]
fig_template.layout = (go.Layout(# general
                                font_family=template_specs['font'],
                                font_size=template_specs['axes_font_size'],
                                plot_bgcolor=template_specs['bg_col'],

                                # x axis
                                xaxis_visible=True,
                                xaxis_color= template_specs['axes_color'],
                                xaxis_showgrid=False,
                                xaxis_ticks="outside",
                                xaxis_ticklen=8,
                                xaxis_tickfont_family=template_specs['font'],
                                xaxis_tickfont_size=template_specs['axes_font_size'],
                                xaxis_zeroline=False,
                                xaxis_zerolinecolor=template_specs['axes_color'],
                                xaxis_zerolinewidth=0,
                                
                                # # y axis
                                yaxis_visible=True,
                                yaxis_linewidth=template_specs['axes_width'],
                                yaxis_color= template_specs['axes_color'],
                                yaxis_showgrid=False,
                                yaxis_ticks="outside",
                                yaxis_ticklen=0,
                                yaxis_tickfont_family=template_specs['font'],
                                yaxis_tickfont_size=template_specs['axes_font_size'],
                                ))

fig_template.layout.annotationdefaults = go.Annotation(
                                font_family=template_specs['font'],
                                font_size=template_specs['axes_font_size'])


In [40]:
def rgb2rgba(input_col,alpha_val):
    rgba_col = "rgba{}, {})".format(rgb_col[3:-1],alpha_val)
    return rgba_col

num_row, num_col = 1,3
sp_width, sp_height = 400, 400

color_list = px.colors.qualitative.Prism
rois_g1 = ['V1','V2','V3']
rois_c1 = [color_list[0],color_list[1],color_list[2]]
rois_g2 = ['V3AB','LO','VO','hMT+']
rois_c2 = [color_list[3],color_list[4],color_list[5],color_list[6]]
rois_g3 = ['iIPS','sIPS','iPCS','sPCS']
rois_c3 = [color_list[7],color_list[8],color_list[9],color_list[10]]

x_titles = [0,0.43,0.87]
rois_groups = [rois_g1,rois_g2,rois_g3]
rois_colors = [rois_c1,rois_c2,rois_c3]
rois_titles = ['<b>Low-level visual areas</b>','<b>Mid-level visual areas</b>','<b>High-level visual areas</b>']
fig = make_subplots(rows=num_row, cols=num_col)

for rois_group_num,(rois_group,rois_color,rois_title,x_title) in enumerate(zip(rois_groups,rois_colors,rois_titles,x_titles)):
    for roi,color in zip(rois_group,rois_color):
        fig.add_violin(y=df[roi], name=roi, span=[0,1], spanmode='manual', fillcolor=color, row=1, col=rois_group_num+1)
        fig.add_annotation(xref="paper", yref="paper", x=x_title, y=1.15, text=rois_title, showarrow=False)

fig.update_layout(showlegend=False,template=fig_template,width = sp_width*num_col,height = sp_height*num_row)
fig.update_yaxes(title_text='R\u00b2', range=[0,1],linewidth=template_specs['axes_width'])
fig.show()

In [79]:
# def rgb2rgba(input_col,alpha_val):
#     rgba_col = "rgba{}, {})".format(rgb_col[3:-1],alpha_val)
#     return rgba_col

sp_height, sp_width = 1000, 1200

rois_colors = px.colors.qualitative.Prism[::-1]
rois = analysis_info['rois'][-2::-1]

posH, posV = 0.5, 0.044
sizeV, sizeH = 0.08, 0.08
spaceV = 0.0832
domains = []

fig = make_subplots(rows=3, cols=5,specs=[[{'rowspan': 3, 'colspan': 2}, None, None, {'colspan': 2}, None],
                                          [None, None, None, {'colspan': 2}, None],
                                          [None, None, None, {'colspan': 2}, None]], 
                                    print_grid=False,
                                    #vertical_spacing=0,
                                    #horizontal_spacing=0
                                    )



for num,(roi,roi_color) in enumerate(zip(rois,rois_colors)):
    fig.add_violin(x = df[roi], name = roi, span = [0,1], orientation = "h", spanmode = 'manual', fillcolor = roi_color, row=1, col=1)
    domain = {'x': [posH, posH+sizeH], 'y': [posV+num*spaceV, posV+num*spaceV+sizeV]}
    
    fig.add_trace(go.Pie(labels = ["A","B"], 
                            values = [10,90],
                            showlegend = False,
                            textposition = ["none","inside"],
                            marker_colors = ['rgba(200,200,200,1)',
                                             roi_color],
                            marker_line_color = ['rgba(200,200,200,1)',
                                                 'rgba(0,0,0,1)'],
                            marker_line_width = [2,
                                                 2],
                            rotation = 0,
                            direction = "clockwise",
                            hole = 0.4,
                            sort = False,
                            domain = domain,
                   ))


trace1 = go.Scatter(x = np.linspace(0, 2, 60),
                    y = np.random.rand(60),
                    mode = 'lines',
                    line = dict(width = 1, color = 'red'))
fig.append_trace(trace1, 1,4)

trace2 = go.Scatter(x = np.linspace(0, 2, 60),
                    y = np.random.rand(60),
                    mode = 'lines',
                    line = dict(width = 1, color = 'red'))
fig.append_trace(trace2, 2,4)

trace3 = go.Scatter(x = np.linspace(0, 2, 60),
                    y = np.random.rand(60),
                    mode = 'lines',
                    line = dict(width = 1, color = 'red'))
fig.append_trace(trace3, 3,4)

fig.update_layout(showlegend=False,template=fig_template,width = sp_width,height = sp_height, margin_l = 70, margin_r = 50, margin_t = 50, margin_b =70)
fig.update_xaxes(title_text='R\u00b2',linewidth=1)
fig.update_yaxes(linewidth=0)
fig.show()

# https://community.plotly.com/t/custom-sized-subplots/10024/5

# to do
# 1. check that pie can be ploted with append_trace, if yes then add 11 rows (or 12)
# 2. compute contra-laterality
# 3. draw fake relation eccentricity size
# 4. compute relation eccentricity size relationship 
# 5. make plot with two entries (condition 1 and 2 => split violoin, make two circle, make 2 sets of lines changing hue)
# 6. make entries slider to pick the condition to plot